In [74]:
import requests, time,shlex,subprocess
import mimetypes as mim
import base64
import pytesseract
from matplotlib.pyplot import imread
import re
page = 1
res =[]
from PIL import Image,ImageFile
import numpy as np
ImageFile.LOAD_TRUNCATED_IMAGES = True

In [75]:
#Send Request to Github API to get the repos links in the json file.
req = requests.get('https://api.github.com/search/repositories?q=fintech microservice created:>2016-01-01 in:paths,file in:description in:readme created:2019-10-01 forks:>1 &page='+str(page),auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5'))


In [76]:
res = req.json()
first=0

In [77]:
res

{'total_count': 10,
 'incomplete_results': False,
 'items': [{'id': 92843802,
   'node_id': 'MDEwOlJlcG9zaXRvcnk5Mjg0MzgwMg==',
   'name': 'fs2-rabbit',
   'full_name': 'profunktor/fs2-rabbit',
   'private': False,
   'owner': {'login': 'profunktor',
    'id': 50294948,
    'node_id': 'MDEyOk9yZ2FuaXphdGlvbjUwMjk0OTQ4',
    'avatar_url': 'https://avatars0.githubusercontent.com/u/50294948?v=4',
    'gravatar_id': '',
    'url': 'https://api.github.com/users/profunktor',
    'html_url': 'https://github.com/profunktor',
    'followers_url': 'https://api.github.com/users/profunktor/followers',
    'following_url': 'https://api.github.com/users/profunktor/following{/other_user}',
    'gists_url': 'https://api.github.com/users/profunktor/gists{/gist_id}',
    'starred_url': 'https://api.github.com/users/profunktor/starred{/owner}{/repo}',
    'subscriptions_url': 'https://api.github.com/users/profunktor/subscriptions',
    'organizations_url': 'https://api.github.com/users/profunktor/orgs',


In [78]:
while (res['items'] != []):
    #print(res)
    time.sleep(10)
    total_count =res['total_count']
    repoDic={}
    repos=res['items']
    for repoIndx in range(first,len(repos)):
            repoName=repos[repoIndx]['full_name'].split('/')[1]
            repoDic[repoName] = {}
            repoDic[repoName]['desc']=repos[repoIndx]['description']
            #We will the contents link for repo by using 'content_url' key.
            contentsUrl = repos[repoIndx]['contents_url']   
            contentsUrl=contentsUrl.split('{+path}')[0]
            #Sending the request to get folders and files 
            gitReq=requests.get(contentsUrl,auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5'))
            contents=gitReq.json()
            time.sleep(5)
            for contentIndx in range(0,len(contents)):
                    #print(contents)
                    # Guessing the extensions of the files by mimtypes.
                    typeGuess = mim.guess_type(contents[contentIndx]['name'])
                    if(typeGuess[0] is not None):
                            typeGuess=typeGuess[0].split('/')
                            typeGuessImg=check_img(typeGuess)
                            #print(typeGuessImg)
                            typeGuess=check_text(typeGuess) or check_img(typeGuess)
                    elif(contents[contentIndx]['type']=='file' and (re.search(contents[contentIndx]['name'],'description') or contents[contentIndx]['name']=='README')):
                            typeGuess = typeGuess[0]
                            gitReq=requests.get(contents[contentIndx]['git_url'],auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5'))
                            fileContent=gitReq.json()
                            fileName=contents[contentIndx]['name']
                            fileBytes=base64.b64decode(fileContent['content'])
                            repoDic[repoName][fileName]=fileBytes.decode('utf-8')
                            time.sleep(3)
                            continue
                    #print(typeGuess)        
                    if(contents[contentIndx]['type']=='file' and typeGuess==True ):
                        gitReq=requests.get(contents[contentIndx]['git_url'],auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5'))
                        fileName=contents[contentIndx]['name']
                        fileContent=gitReq.json()
                        fileBytes=base64.b64decode(fileContent['content'])
                        #print(typeGuessImg)
                        if(typeGuessImg):  
                                #print(fileBytes)
                                if(fileName.split('.')[-1] == 'SVG' or  fileName.split('.')[-1] == 'svg'):
                                           continue
                                imgFile=open('ImgToSave.'+fileName.split('.')[-1],'wb')
                                #imgFile=open(fileName)
                                imgFile.write(fileBytes)
                                imgFile.close()
                                #Extract the text from the image.
                                '''
                                imgFile=Image.open(fileName,'r').convert('RGB')
                                pixels=np.asarray(imgFile,np.uint8)
                                print(pixels.shape)
                                convertedImg=abs(np.fft.rfft2(pixels,axes=(0,1)))
                                print(convertedImg.shape)
                                convertedImg=np.uint8(convertedImg)
                                imgFile=Image.fromarray(convertedImg)
                                imgFile.save(fileName)
                                '''    
                                if(fileName.split('.')[-1]=='png'or fileName.split('.')[-1]=='PNG'):
                                            imgFile=Image.open('ImgToSave.'+fileName.split('.')[-1],'r').convert('RGB')
                                            imgFile.save('ImgToSave.jpg')
                                            fileName='ImgToSave.jpg'
                                textOfImg=pytesseract.image_to_string(imread('ImgToSave.'+fileName.split('.')[-1]))
                                repoDic[repoName][fileName]=textOfImg
                        else:
                                repoDic[repoName][fileName]=fileBytes.decode('utf-8')
                                  
                    elif(contents[contentIndx]['type']=='dir'): 
                                dirContents=requests.get(contents[contentIndx]['git_url']+'?recursive=-1',auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5'))
                                files= dirContents.json()['tree']
                                #print(files)
                                time.sleep(3)
                                for fileIndx in range(len(files)):
                                        #print(files[fileIndx])
                                        if(files[fileIndx]['type']=='tree'):
                                            continue
                                        typeGuess = mim.guess_type(files[fileIndx]['path'])
                                        if(typeGuess[0] is not None):
                                            typeGuess=typeGuess[0].split('/')
                                            #print(typeGuess)
                                            typeGuessImg=check_img(typeGuess)    
                                            typeGuess= check_text(typeGuess) or check_img(typeGuess)
                                           
                                        elif(files[fileIndx]['type']=='blob' and (re.search(files[fileIndx]['path'],'description') or files[fileIndx]['path'].split('/')[-1]=='README')):
                                            typeGuess=typeGuess[0]
                                            fileContent=requests.get(files[fileIndx]['url'],auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5'))
                                            fileName=files[fileIndx]['path'].split('/')[-1]
                                            repoDic[repoName][fileName]=fileBytes.decode('utf-8')
                                            time.sleep(3)
                                            continue
                                        print(files[fileIndx])    
                                        if(files[fileIndx]['type']=='blob' and typeGuess==True):
                                                fileContent=requests.get(files[fileIndx]['url'],auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5')) 
                                                fileContent=fileContent.json()
                                                #print(fileContent)
                                                fileName=files[fileIndx]['path'].split('/')[-1]
                                                fileBytes=base64.b64decode(fileContent['content']) 
                                                #print(typeGuessImg)
                                                if(typeGuessImg):  
                                                    #print(fileBytes)
                                                    if(fileName.split('.')[-1] == 'SVG' or  fileName.split('.')[-1] == 'svg'):
                                                             continue
                                                    imgFile=open('ImgToSave.'+fileName.split('.')[-1],'wb')
                                                    imgFile.write(fileBytes)
                                                    imgFile.close()
                                                    #Extract the text from the image.
                                                    '''                                                    
                                                    imgFile=Image.open(fileName,'r').convert('RGB')
                                                    pixels=np.asarray(imgFile,np.uint8)
                                                    print(pixels.shape)
                                                    convertedImg=abs(np.fft.rfft2(pixels,axes=(0,1)))
                                                    print(convertedImg.shape)
                                                    convertedImg=np.uint8(convertedImg)
                                                    imgFile=Image.fromarray(convertedImg)
                                                    imgFile.save(fileName)
                                                    '''    
                                                    if(fileName.split('.')[-1]=='png'or fileName.split('.')[-1]=='PNG'):
                                                            imgFile=Image.open('ImgToSave.'+fileName.split('.')[-1],'r').convert('RGB')
                                                            imgFile.save('ImgToSave.jpg')
                                                            fileName='ImgToSave.jpg'
                                                            
                                                    textOfImg=pytesseract.image_to_string(imread('ImgToSave.'+fileName.split('.')[-1]))
                                                    
                                                    repoDic[repoName][fileName]=textOfImg
                                                else:
                                                    repoDic[repoName][fileName]=fileBytes.decode('utf-8')
                                                    
                                                time.sleep(12)
            repoFile = open(repoName,'w')
            repoFile.write(str(repoDic))
            repoFile.close()
            repoDic={}
    page +=1
    req = requests.get('https://api.github.com/search/repositories?q=fintech microservice created:>2016-01-01 in:paths,file in:description in:readme created:2019-10-01 forks:>1 &page='+str(page),auth=('glmess','d1913d2878315aae97fffd3aaaed36b16489d1e5'))
    res = req.json()      
    first=0
     

{'path': 'config.yml', 'mode': '100644', 'type': 'blob', 'sha': 'd072484d8c9a2643cee84c422df5095b45e30fb4', 'size': 1217, 'url': 'https://api.github.com/repos/profunktor/fs2-rabbit/git/blobs/d072484d8c9a2643cee84c422df5095b45e30fb4'}
{'path': 'FUNDING.yml', 'mode': '100644', 'type': 'blob', 'sha': '78c324252951687cce38d62622c7819929563ee4', 'size': 581, 'url': 'https://api.github.com/repos/profunktor/fs2-rabbit/git/blobs/78c324252951687cce38d62622c7819929563ee4'}

{'path': 'src/main/scala-2.11/dev/profunktor/fs2rabbit/javaConversion.scala', 'mode': '100644', 'type': 'blob', 'sha': 'e4a4fd2fda1a9954ee95d5ce525512fa6bd1c3c0', 'size': 1037, 'url': 'https://api.github.com/repos/profunktor/fs2-rabbit/git/blobs/e4a4fd2fda1a9954ee95d5ce525512fa6bd1c3c0'}
{'path': 'src/main/scala-2.12/dev/profunktor/fs2rabbit/javaConversion.scala', 'mode': '100644', 'type': 'blob', 'sha': 'e4a4fd2fda1a9954ee95d5ce525512fa6bd1c3c0', 'size': 1037, 'url': 'https://api.github.com/repos/profunktor/fs2-rabbit/git/bl

{'path': 'src/test/scala/dev/profunktor/fs2rabbit/AmqpFieldValueSpec.scala', 'mode': '100644', 'type': 'blob', 'sha': '6c0adb36319af2194e6dd646ec4d265bc57a7636', 'size': 4928, 'url': 'https://api.github.com/repos/profunktor/fs2-rabbit/git/blobs/6c0adb36319af2194e6dd646ec4d265bc57a7636'}
{'path': 'src/test/scala/dev/profunktor/fs2rabbit/AmqpPropertiesSpec.scala', 'mode': '100644', 'type': 'blob', 'sha': '2bf6cbd7c8eda4741155284bf08b369d45758ceb', 'size': 6901, 'url': 'https://api.github.com/repos/profunktor/fs2-rabbit/git/blobs/2bf6cbd7c8eda4741155284bf08b369d45758ceb'}
{'path': 'src/test/scala/dev/profunktor/fs2rabbit/SafeArgSpec.scala', 'mode': '100644', 'type': 'blob', 'sha': 'b8a3d1aabdbc4838122d4ef390044731451ab119', 'size': 2858, 'url': 'https://api.github.com/repos/profunktor/fs2-rabbit/git/blobs/b8a3d1aabdbc4838122d4ef390044731451ab119'}
{'path': 'src/test/scala/dev/profunktor/fs2rabbit/effects/EnvelopeDecoderSpec.scala', 'mode': '100644', 'type': 'blob', 'sha': '56d0a982f55e476

TesseractNotFoundError: tesseract is not installed or it's not in your path

In [70]:
def check_text(typeGuess):
    if(re.search(typeGuess[0],'text') or re.search(typeGuess[1],'json') or re.search(typeGuess[1],'javascript')):
         return True
    else:
         return False

In [71]:
def check_img(typeGuess):
    print()
    if(re.search(typeGuess[0],'image')):
         return True
    else:
         return False

In [72]:
mim.guess_type('app.js')

('application/javascript', None)

In [73]:
check_text(typeGuess)

TypeError: 'bool' object is not subscriptable

In [54]:
False !=None

True

In [55]:
mim.guess_type('.gitignore')

(None, None)

In [56]:
len('README'.split('/')[-1])

6

In [57]:
'gjgjgjgjgg/.gitignore'.split('.')

['gjgjgjgjgg/', 'gitignore']

In [58]:
(None,None)!=None

True

In [59]:
'george'.upper()

'GEORGE'

In [60]:
import base64


b=base64.b64decode("...\nAElFTkSuQmCC\n")

In [61]:
b

b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x06\x18\x00\x00\x03\x0b\x08\x02\x00\x00\x003\n\nD\x00\x00\x00\x01sRGB\x00\xae\xce\x1c\xe9\x00\x00\x00\x04gAMA\x00\x00\xb1\x8f\x0b\xfca\x05\x00\x00\x00\tpHYs\x00\x00\x0e\xc3\x00\x00\x0e\xc3\x01\xc7o\xa8d\x00\x00\xa27IDATx^\xed\xfd\x0b\xb4eUa\xe7\xfb\xdf1z\x8c\x1ew\xe4\xa1\x9d\x7f\xa7\xfb\x9ax3\xfa&\xe9\x9b\xbe7\x06\xedN\xd2b\x12;\x89\x9a\x18\x13\x93\xdcN\x04\x15h_Q\n,\xa0\nAAy(H\x15\x02\xbe\xc0\x17\x88\x8a\xf2\x10\x0c\x85\x06\x10\x10\xa4\x02>@\xa8\x02\n\x05\x15\x94g\x15\x05EU\xf1\xa8\x02\n\x8a\x82\x82\xff\xdc{\xae=\xf7\\s\xaf\xbd\xcf>\xa7N\x9dsV\x9d\xcfw|G\x8d\xbd\xe6\x9ek\xae\xb9\xd6\x9ag\x9d5\x7f\xb5\xf6>\xff\xdb\x0bv\xdb\x9d$I\x92$I\x92\x9cPA\x12I\x92$I\x92$\xc7R\x90D\x92$I\x92$\xc9\xb1\x14$\x91$I\x92$Ir,\x05I$I\x92$I\x92\x1cKA\x12I\x92$I\x92$\xc7R\x90D\x92$I\x92$\xc9\xb1\x14$\x91$I\x92$Ir,\x05I$I\x92$I\x92\x1cKA\x12I\x92$I\x92$\xc7R\x90D\x92$I\x92$\xc9\xb1\x14$\x91$I\x92$Ir,\x05I$I\x92$I\x92\x1cKA\x12I\x92$I\x92\xe4<\xf2?\xbf\xf2/\x16\x1

In [62]:
b=open('B.png','wb')

In [63]:
import sys

In [64]:
print(sys.getsizeof(b))

4272


In [40]:
repoDic

{'iot-device-simulator': {'desc': 'The IoT Device Simulator solution is a Graphical User Interface (GUI) based engine designed to enable customers to get started quickly assessing AWS IoT services without an existing pool of devices. The IoT Device Simulator helps effortlessly create and simulate thousands of connected devices that are defined by the customer.',
  'app.js': '/*********************************************************************************************************************\n *  Copyright 2016 Amazon.com, Inc. or its affiliates. All Rights Reserved.                                           *\n *                                                                                                                    *\n *  Licensed under the Amazon Software License (the "License"). You may not use this file except in compliance        *\n *  with the License. A copy of the License is located at                                                             *\n *                

In [42]:
repoDic

{'iot-device-simulator': {'desc': 'The IoT Device Simulator solution is a Graphical User Interface (GUI) based engine designed to enable customers to get started quickly assessing AWS IoT services without an existing pool of devices. The IoT Device Simulator helps effortlessly create and simulate thousands of connected devices that are defined by the customer.',
  'app.js': '/*********************************************************************************************************************\n *  Copyright 2016 Amazon.com, Inc. or its affiliates. All Rights Reserved.                                           *\n *                                                                                                                    *\n *  Licensed under the Amazon Software License (the "License"). You may not use this file except in compliance        *\n *  with the License. A copy of the License is located at                                                             *\n *                

In [43]:
file=open('Dicrepo_2.txt','w')

In [44]:
file.write(str(repoDic))

3583078